# Password counts

Download 1.4 billion password breach compilation wordlist:

https://gist.github.com/scottlinux/9a3b11257ac575e4f71de811322ce6b3

remove lines containing non-alphanumeric characters:

`$ sed -i '/[^[:alnum:]_@]/d' passwd`

sort alphabetically:

`$ sort passwd`


remove duplicate lines:

`$ awk '!visited[$0]++' passwd > passwd`

split into files with a maximum file size of 3333 Mb:

`$ split -C 3333m --numeric-suffixes passwd > passwd`

count number of occurrence of each line:

`$ uniq -c passwd`

remove leading whitespaces:

`$ sed -e 's/^ *//' passwd`

add index line to the beginning of the file:
    
`$ echo 'count password' | cat - passwd > temp && mv temp passwd`

In [164]:
import pandas as pd

from os import walk
from tqdm import tqdm  # taqaddum (progress)
from wordcloud import WordCloud

In [165]:
_, _, filenames = next(walk('data'))
sorted(filenames)

['passwd_counts_00', 'passwd_counts_01', 'passwd_counts_02']

In [166]:
for index, file in tqdm(enumerate(filenames)):
    df = pd.read_csv('data/'+file, delimiter=' ')
    df_sorted = df.sort_values('count')
    df_sorted.to_csv('data/csv/sorted_counts_0'+str(index)+'.csv', index=False)
    del df, df_sorted

3it [13:16, 265.35s/it]


In [167]:
_, _, filenames = next(walk('data/csv'))
sorted(filenames)

['sorted_counts_00.csv', 'sorted_counts_01.csv', 'sorted_counts_02.csv']

In [168]:
max_frames = []
for index, file in tqdm(enumerate(filenames)):
    df = pd.read_csv('data/csv/'+file, delimiter=',')
    df_max = df.nlargest(333, ['count'])  # nsmallest
    max_frames.append(df_max)
    df_max.to_csv('data/csv/max_counts_0'+str(index)+'.csv', index=False)
    del df, df_max

3it [05:14, 104.77s/it]


In [169]:
max_frame = pd.concat(max_frames)
max_frame_sorted = max_frame.sort_values('count')
max_frame_sorted.to_csv('data/csv/passwd_counts.csv', index=False)

# max_frame_sorted = pd.read_csv('data/csv/passwd_counts.csv', delimiter=',')

df_max = max_frame_sorted.nlargest(100, ['count']).reset_index(drop=True)
dict_max = df_max.set_index('password').to_dict()

It seems that a bug in python requires me to do the following:

In [211]:
my_dict = dict(zip([key for key in dict_max['count'].keys()], [val for val in dict_max['count'].values()]))

In [212]:
WordCloud(max_words=100).generate_from_frequencies(my_dict).to_svg()

'<svg xmlns="http://www.w3.org/2000/svg" width="400" height="200">\n<style>text{font-family:\'Droid Sans Mono\';font-weight:normal;font-style:normal;}</style>\n<rect width="100%" height="100%" style="fill:black"></rect>\n<text transform="translate(58,150)" font-size="88" style="fill:rgb(246, 230, 32)">123456</text>\n<text transform="translate(3,61)" font-size="59" style="fill:rgb(58, 186, 118)">123456789</text>\n<text transform="translate(68,181)" font-size="42" style="fill:rgb(72, 36, 117)">111111</text>\n<text transform="translate(212,181)" font-size="39" style="fill:rgb(36, 170, 131)">password</text>\n<text transform="translate(29,193) rotate(-90)" font-size="37" style="fill:rgb(70, 7, 90)">qwerty</text>\n<text transform="translate(308,78)" font-size="25" style="fill:rgb(76, 194, 108)">abc123</text>\n<text transform="translate(126,79)" font-size="23" style="fill:rgb(39, 128, 142)">12345678</text>\n<text transform="translate(41,79)" font-size="15" style="fill:rgb(62, 74, 137)">passwo